### 모델 학습 - 1차 경로

In [1]:
import pandas as pd
import random
from datetime import datetime, timedelta

# INPUT.xlsx 로드
input_df = pd.read_excel("INPUT.xlsx")

# 랜덤한 departure_time 생성 함수
def generate_random_time(start_date, end_date):
    # 시작 날짜와 끝 날짜를 datetime 객체로 변환
    start = datetime.strptime(start_date, "%Y-%m-%d %H:%M:%S")
    end = datetime.strptime(end_date, "%Y-%m-%d %H:%M:%S")
    
    # 랜덤 시간 생성 (한 시간 단위)
    random_seconds = random.randint(0, int((end - start).total_seconds() // 3600)) * 3600
    random_time = start + timedelta(seconds=random_seconds)
    return random_time

# 날짜 범위 설정
start_date = "2024-11-19 00:00:00"
end_date = "2024-11-20 23:59:59"

# 각 행에 대해 departure_time 생성
input_df['departure_time'] = input_df.apply(lambda _: generate_random_time(start_date, end_date), axis=1)

# 결과 확인
print(input_df[['user_id', 'departure_time']].head())

# 수정된 INPUT.xlsx 저장
input_df.to_excel("INPUT_with_departure_time.xlsx", index=False)
print("INPUT_with_departure_time.xlsx 파일이 저장되었습니다.")

   user_id      departure_time
0      412 2024-11-20 09:00:00
1      399 2024-11-20 00:00:00
2      426 2024-11-19 12:00:00
3      432 2024-11-19 10:00:00
4      297 2024-11-20 23:00:00
INPUT_with_departure_time.xlsx 파일이 저장되었습니다.


In [21]:
import pandas as pd

input_df = pd.read_excel("../INPUT.xlsx")
first_route_df = pd.read_excel("../Temp_Result/First_Route.xlsx")
product_df = pd.read_excel("../Dataset/PRODUCT.xlsx")

# user_id, departure, destination을 이용하여 위경도 값 추출 함수
def get_lat_long_from_input(user_id, departure, destination, input_df):
    # 해당 user_id에 해당하는 데이터 찾기
    user_data = input_df[(input_df['user_id'] == user_id) &
                         (input_df['departure'] == departure) &
                         (input_df['destination'] == destination)]
    
    if not user_data.empty:
        # 위도와 경도 값 반환
        departure_lat = user_data.iloc[0]['departure_lat']
        departure_long = user_data.iloc[0]['departure_long']
        destination_lat = user_data.iloc[0]['destination_lat']
        destination_long = user_data.iloc[0]['destination_long']
        
        max_weight = user_data.iloc[0]['max_weight']
        min_weight = user_data.iloc[0]['min_weight']
        preference = user_data.iloc[0]['preference']
        departure_time = user_data.iloc[0]['departure_time']
        return departure_lat, departure_long, destination_lat, destination_long, max_weight, min_weight, preference, departure_time
    else:
        # 일치하는 값이 없으면 None 반환
        return None, None, None, None, None, None, None, None
    
def get_lat_long_from_product(product_id):
    prod_data = product_df[(product_df['product_id'] == product_id)]
    
    if not prod_data.empty:
        departure_lat = prod_data.iloc[0]['departure_lat']
        departure_long = prod_data.iloc[0]['departure_long']
        destination_lat = prod_data.iloc[0]['destination_lat']
        destination_long = prod_data.iloc[0]['destination_long']
        return departure_lat, departure_long, destination_lat, destination_long
    else:
        return None, None, None, None

# 'First_Route.xlsx'에 위경도 정보 추가
first_route_df[['departure_lat', 'departure_long', 'destination_lat', 'destination_long', 'max_weight', 'min_weight', 'preference', 'departure_time']] = first_route_df.apply(
    lambda row: pd.Series(get_lat_long_from_input(row['user_id'], row['departure'], row['destination'], input_df)),
    axis=1
)

# 'main_product_id' 기준으로 main_departure_lat, main_departure_long 추가
first_route_df[['prod_departure_lat', 'prod_departure_long', 'prod_destination_lat', 'prod_destination_long']] = first_route_df.apply(
    lambda row: pd.Series(get_lat_long_from_product(row['product_id'])),
    axis=1
)

# 학습 데이터(X) 준비
X = first_route_df[['departure_lat', 'departure_long', 'destination_lat', 'destination_long', 'max_weight', 'min_weight', 'preference', 'departure_time']]
y = first_route_df[['prod_departure_lat', 'prod_departure_long', 'prod_destination_lat', 'prod_destination_long']]  # 메인 경로의 출발지

# 데이터 확인
X.head()
y.head()

prod_departure_lat  prod_departure_long  prod_destination_lat  \
0           37.154360           127.118477             35.422210   
1           37.336523           127.098432             35.433139   
2           37.154360           127.118477             35.433139   
3           37.256459           127.381227             34.813631   
4           37.176465           127.179518             34.752175   

   prod_destination_long  
0             127.325232  
1             127.328596  
2             127.328596  
3             126.373800  
4             126.360594

In [25]:
import pandas as pd
import numpy as np
import joblib
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split

X = X.copy()
X['departure_time'] = pd.to_datetime(X['departure_time']).view(int) / 10**9

# 데이터 스케일링 (정규화 또는 표준화)
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X[['departure_lat', 'departure_long', 'destination_lat', 
                                   'destination_long', 'preference']])

joblib.dump(scaler, 'scaler.pkl') 

# Step 5: 데이터셋 나누기 (train, validation, test)
X_train, X_temp, y_train, y_temp = train_test_split(X_scaled, y, test_size=0.3, random_state=42)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.5, random_state=42)

# Step 6: 데이터 확인
print("\n훈련 데이터 크기:", X_train.shape, y_train.shape)
print("검증 데이터 크기:", X_val.shape, y_val.shape)
print("테스트 데이터 크기:", X_test.shape, y_test.shape)


훈련 데이터 크기: (16650, 5) (16650, 4)
검증 데이터 크기: (3568, 5) (3568, 4)
테스트 데이터 크기: (3568, 5) (3568, 4)


In [23]:
import xgboost as xgb
from sklearn.metrics import mean_squared_error, mean_absolute_error
import numpy as np

# XGBoost 데이터 포맷으로 변환
dtrain = xgb.DMatrix(X_train, label=y_train)
dval = xgb.DMatrix(X_val, label=y_val)
dtest = xgb.DMatrix(X_test, label=y_test)

# XGBoost 파라미터 설정
params = {
    'objective': 'reg:squarederror',  # 회귀 문제
    'eval_metric': 'rmse',           # 평가 지표로 RMSE 사용
    'max_depth': 8,                  # 트리 깊이
    'eta': 0.01,                     # 학습률
    'subsample': 0.8,                # 데이터 샘플링 비율
    'colsample_bytree': 0.8,         # 특성 샘플링 비율
    'seed': 42                       # 재현성 확보
}

# 학습
evals = [(dtrain, 'train'), (dval, 'validation')]
model = xgb.train(
    params=params,
    dtrain=dtrain,
    num_boost_round=700,             # 부스팅 반복 횟수
    evals=evals,
    early_stopping_rounds=20,        # 조기 종료
    verbose_eval=10                  # 10번마다 학습 상황 출력
)

model.save_model('First_Route_Model.json')  
# 테스트 데이터 예측
y_pred = model.predict(dtest)

# 평가 지표 계산
mse = mean_squared_error(y_test, y_pred)
mae = mean_absolute_error(y_test, y_pred)

print(f"\n테스트 손실(MSE): {mse:.4f}")
print(f"테스트 MAE: {mae:.4f}")

# 예측값과 실제값 비교 (테스트 데이터 일부 출력)
for i in range(5):
    print(f"\n테스트 데이터 {i+1}:")
    print(f"실제값 (y_test): {y_test.iloc[i].values}")
    print(f"예측값 (y_pred): {y_pred[i]}")


[0]	train-rmse:45.21903	validation-rmse:45.23225
[10]	train-rmse:40.89641	validation-rmse:40.90910
[20]	train-rmse:36.98706	validation-rmse:36.99920
[30]	train-rmse:33.45148	validation-rmse:33.46314
[40]	train-rmse:30.25393	validation-rmse:30.26514
[50]	train-rmse:27.36201	validation-rmse:27.37261
[60]	train-rmse:24.74649	validation-rmse:24.75643
[70]	train-rmse:22.38107	validation-rmse:22.39037
[80]	train-rmse:20.24191	validation-rmse:20.25074
[90]	train-rmse:18.30709	validation-rmse:18.31536
[100]	train-rmse:16.55730	validation-rmse:16.56506
[110]	train-rmse:14.97478	validation-rmse:14.98204
[120]	train-rmse:13.54365	validation-rmse:13.55052
[130]	train-rmse:12.24934	validation-rmse:12.25590
[140]	train-rmse:11.07865	validation-rmse:11.08480
[150]	train-rmse:10.01994	validation-rmse:10.02568
[160]	train-rmse:9.06246	validation-rmse:9.06781
[170]	train-rmse:8.19650	validation-rmse:8.20145
[180]	train-rmse:7.41334	validation-rmse:7.41793
[190]	train-rmse:6.70504	validation-rmse:6.70929

In [24]:
import numpy as np
import pandas as pd

# PRODUCT.xlsx 데이터 로드
product_df = pd.read_excel("../Dataset/PRODUCT.xlsx")

# 유클리드 거리 계산 함수 (두 점 사이의 거리 계산)
def calculate_distance(lat1, lon1, lat2, lon2):
    return np.sqrt((lat1 - lat2)**2 + (lon1 - lon2)**2)

# 예측값과 가장 가까운 상품 매칭
def match_closest_product(pred_departure_lat, pred_departure_lon, pred_destination_lat, pred_destination_lon, product_df):
    # 상품들의 출발지, 목적지 위도, 경도
    product_departure_latitudes = product_df['departure_lat']
    product_departure_longitudes = product_df['departure_long']
    product_destination_latitudes = product_df['destination_lat']
    product_destination_longitudes = product_df['destination_long']
    
    # 예측값과 각 상품의 출발지, 목적지 간의 거리 계산
    departure_distances = np.array([calculate_distance(pred_departure_lat, pred_departure_lon, lat, lon) 
                                    for lat, lon in zip(product_departure_latitudes, product_departure_longitudes)])
    destination_distances = np.array([calculate_distance(pred_destination_lat, pred_destination_lon, lat, lon)
                                      for lat, lon in zip(product_destination_latitudes, product_destination_longitudes)])

    # 출발지와 목적지의 평균 거리를 계산하여 가장 가까운 상품을 찾기
    total_distances = departure_distances + destination_distances
    closest_index = np.argmin(total_distances)
    
    # 해당 상품 정보 반환
    closest_product = product_df.iloc[closest_index]
    return closest_product

# 예측값(y_pred)와 실제값(y_test) 비교 (테스트 데이터 일부 출력)
def compare_predictions_and_actuals(n=10):
    for i in range(n):
        predicted_departure_lat, predicted_departure_lon, predicted_destination_lat, predicted_destination_lon = y_pred[i]
        
        print(f"\n테스트 데이터 {i+1}:")
        print(f"실제값 (y_test): {y_test.iloc[i].values}")
        print(f"예측값 (y_pred): {predicted_departure_lat}, {predicted_departure_lon}, {predicted_destination_lat}, {predicted_destination_lon}")
        
        # 가장 가까운 상품 매칭
        closest_product = match_closest_product(predicted_departure_lat, predicted_departure_lon, 
                                                predicted_destination_lat, predicted_destination_lon, 
                                                product_df)
        
        print(f"\n가장 가까운 상품 (예측값과 매칭):")
        print(closest_product[['product_id', 'departure_lat', 'departure_long', 'destination_lat', 'destination_long']])

        # PRODUCT.xlsx에서 해당 product_id로 한글 주소 가져오기
        product_info = product_df[product_df['product_id'] == closest_product['product_id']].iloc[0]
        product_departure = product_info['departure']
        product_destination = product_info['destination']
        
        print(f"가장 가까운 상품의 한글 주소:")
        print(f"상품 출발지: {product_departure}")
        print(f"상품 목적지: {product_destination}")
        
        # 실제값(y_test)의 departure_lat, departure_long, destination_lat, destination_long
        actual_departure_lat = y_test.iloc[i]['prod_departure_lat']
        actual_departure_lon = y_test.iloc[i]['prod_departure_long']
        actual_destination_lat = y_test.iloc[i]['prod_destination_lat']
        actual_destination_lon = y_test.iloc[i]['prod_destination_long']

        # 가장 가까운 상품 매칭을 위해 PRODUCT.xlsx에서 실제값과 가장 유사한 출발지, 목적지 찾기
        closest_actual_product = match_closest_product(actual_departure_lat, actual_departure_lon, 
                                                       actual_destination_lat, actual_destination_lon, 
                                                       product_df)
        
        # 실제값의 한글 주소 출력
        actual_product_info = product_df[product_df['product_id'] == closest_actual_product['product_id']].iloc[0]
        actual_product_departure = actual_product_info['departure']
        actual_product_destination = actual_product_info['destination']
        
        print(f"실제값의 한글 주소:")
        print(f"상품 출발지: {actual_product_departure}")
        print(f"상품 목적지: {actual_product_destination}")

# 예시: 10개 데이터 출력
compare_predictions_and_actuals(n=10)


테스트 데이터 1:
실제값 (y_test): [ 37.20422652 127.3514854   35.93008246 128.86738764]
예측값 (y_pred): 37.2045783996582, 127.14633178710938, 35.92527389526367, 128.7880401611328

가장 가까운 상품 (예측값과 매칭):
product_id                5505
departure_lat        37.230093
departure_long      127.118442
destination_lat      35.930082
destination_long    128.867388
Name: 5504, dtype: object
가장 가까운 상품의 한글 주소:
상품 출발지: 경기도 용인시 기흥구 고매로 80, 동원물류 고매 농수산물종합유통센터 지상 2층 (고매동)
상품 목적지: 경상북도 칠곡군 지천면 금호로 272, 사동 (영남복합물류)
실제값의 한글 주소:
상품 출발지: 경기도 이천시 마장면 청강가창로 309, A동
상품 목적지: 경상북도 칠곡군 지천면 금호로 272(4동 영남권내륙화물기지화물하역장)

테스트 데이터 2:
실제값 (y_test): [ 37.30725658 127.46453119  34.9868756  126.7046787 ]
예측값 (y_pred): 37.307594299316406, 127.30522155761719, 34.881935119628906, 126.40768432617188

가장 가까운 상품 (예측값과 매칭):
product_id                5068
departure_lat        37.327355
departure_long        127.3375
destination_lat      34.775338
destination_long    126.425092
Name: 5067, dtype: object
가장 가까운 상품의 한글 주소:
상품 출발지: 경기도 광주시 도척면 도

### 모델 학습 - 1차 경유지

In [21]:
import pandas as pd

stopover_df = pd.read_excel("Temp_Result/First_Stopover.xlsx")

def get_lat_long_from_input(departure, destination, input_df):
    # 해당 user_id에 해당하는 데이터 찾기
    user_data = input_df[(input_df['departure'] == departure) &
                         (input_df['destination'] == destination)]
    
    if not user_data.empty:
        # 위도와 경도 값 반환
        departure_lat = user_data.iloc[0]['departure_lat']
        departure_long = user_data.iloc[0]['departure_long']
        destination_lat = user_data.iloc[0]['destination_lat']
        destination_long = user_data.iloc[0]['destination_long']
        
        max_weight = user_data.iloc[0]['max_weight']
        min_weight = user_data.iloc[0]['min_weight']
        preference = user_data.iloc[0]['preference']
        departure_time = user_data.iloc[0]['departure_time']
        return departure_lat, departure_long, destination_lat, destination_long, max_weight, min_weight, preference, departure_time
    else:
        # 일치하는 값이 없으면 None 반환
        return None, None, None, None, None, None, None, None
    
def get_lat_long_from_product(product_id):
    prod_data = product_df[(product_df['product_id'] == product_id)]
    
    if not prod_data.empty:
        departure_lat = prod_data.iloc[0]['departure_lat']
        departure_long = prod_data.iloc[0]['departure_long']
        destination_lat = prod_data.iloc[0]['destination_lat']
        destination_long = prod_data.iloc[0]['destination_long']
        return departure_lat, departure_long, destination_lat, destination_long
    else:
        return None, None, None, None
    

# 'First_Route.xlsx'에 위경도 정보 추가
stopover_df[['main_departure_lat', 'main_departure_long', 'main_destination_lat', 'main_destination_long', 'max_weight', 'min_weight', 'preference', 'departure_time']] = stopover_df.apply(
    lambda row: pd.Series(get_lat_long_from_input(row['main_departure'], row['main_destination'], input_df)),
    axis=1
)

# 'main_product_id' 기준으로 main_departure_lat, main_departure_long 추가
stopover_df[['prod_departure_lat', 'prod_departure_long', 'prod_destination_lat', 'prod_destination_long']] = stopover_df.apply(
    lambda row: pd.Series(get_lat_long_from_product(row['main_product_id'])),
    axis=1
)

# 'main_product_id' 기준으로 main_departure_lat, main_departure_long 추가
stopover_df[['stopover_departure_lat', 'stopover_departure_long', 'stopover_destination_lat', 'stopover_destination_long']] = stopover_df.apply(
    lambda row: pd.Series(get_lat_long_from_product(row['stopover_product_id'])),
    axis=1
)


# 입력 데이터 (Driver 경로와 1차 물류 경로)
X = stopover_df[['main_departure_lat', 'main_departure_long', 
                 'main_destination_lat', 'main_destination_long', 
                 'prod_departure_lat', 'prod_departure_long', 
                 'prod_destination_lat', 'prod_destination_long']]

# 출력 데이터 (1차 경유지 경로)
y = stopover_df[['stopover_departure_lat', 'stopover_departure_long',
                 'stopover_destination_lat', 'stopover_destination_long']]

# 데이터셋 나누기 (train, validation, test)
X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.3, random_state=42)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.5, random_state=42)

# 데이터 확인
print("\n훈련 데이터 크기:", X_train.shape, y_train.shape)
print("검증 데이터 크기:", X_val.shape, y_val.shape)
print("테스트 데이터 크기:", X_test.shape, y_test.shape)


훈련 데이터 크기: (16576, 8) (16576, 4)
검증 데이터 크기: (3552, 8) (3552, 4)
테스트 데이터 크기: (3552, 8) (3552, 4)


In [26]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_squared_error, mean_absolute_error
import xgboost as xgb

# 정규화
x_scaler = MinMaxScaler()
y_scaler = MinMaxScaler()

X_train_scaled = x_scaler.fit_transform(X_train)
joblib.dump(x_scaler, 'stopover_scaler.pkl') 

X_val_scaled = x_scaler.transform(X_val)
X_test_scaled = x_scaler.transform(X_test)

y_train_scaled = y_scaler.fit_transform(y_train)
y_val_scaled = y_scaler.transform(y_val)
y_test_scaled = y_scaler.transform(y_test)

# XGBoost 데이터 포맷으로 변환
dtrain = xgb.DMatrix(X_train_scaled, label=y_train_scaled)
dval = xgb.DMatrix(X_val_scaled, label=y_val_scaled)
dtest = xgb.DMatrix(X_test_scaled, label=y_test_scaled)

# 모델 파라미터 설정
params = {
    'objective': 'reg:squarederror',  # 회귀 문제
    'max_depth': 6,                   # 트리의 깊이
    'eta': 0.01,                       # 학습률
    'subsample': 0.8,                 # 데이터 샘플링 비율
    'colsample_bytree': 0.8,          # 특성 샘플링 비율
    'seed': 42,                       # 재현성 확보
    'eval_metric': 'rmse'             # 평가 지표: RMSE
}

# 학습
evals = [(dtrain, 'train'), (dval, 'validation')]
model = xgb.train(
    params,
    dtrain,
    num_boost_round=500,
    evals=evals,
    early_stopping_rounds=20,
    verbose_eval=10
)

model.save_model('First_Stopover_Model.json')  

# 테스트 데이터 예측
y_pred_scaled = model.predict(dtest)

# 예측값 원래 스케일로 복원
y_pred = y_scaler.inverse_transform(y_pred_scaled.reshape(-1, y_train.shape[1]))

# 모델 평가
mse = mean_squared_error(y_test, y_pred)
mae = mean_absolute_error(y_test, y_pred)

print(f"\n테스트 손실(MSE): {mse:.4f}")
print(f"테스트 MAE: {mae:.4f}")

# 예측값과 실제값 비교
for i in range(5):
    print(f"\n테스트 데이터 {i+1}:")
    print(f"실제값 (y_test): {y_test.iloc[i].values}")
    print(f"예측값 (y_pred): {y_pred[i]}")

[0]	train-rmse:0.29419	validation-rmse:0.29341
[10]	train-rmse:0.26804	validation-rmse:0.26736
[20]	train-rmse:0.24398	validation-rmse:0.24339
[30]	train-rmse:0.22192	validation-rmse:0.22141
[40]	train-rmse:0.20211	validation-rmse:0.20168
[50]	train-rmse:0.18434	validation-rmse:0.18399
[60]	train-rmse:0.16853	validation-rmse:0.16825
[70]	train-rmse:0.15368	validation-rmse:0.15346
[80]	train-rmse:0.14057	validation-rmse:0.14041
[90]	train-rmse:0.12813	validation-rmse:0.12802
[100]	train-rmse:0.11727	validation-rmse:0.11722
[110]	train-rmse:0.10752	validation-rmse:0.10751
[120]	train-rmse:0.09856	validation-rmse:0.09859
[130]	train-rmse:0.09080	validation-rmse:0.09087
[140]	train-rmse:0.08355	validation-rmse:0.08365
[150]	train-rmse:0.07665	validation-rmse:0.07680
[160]	train-rmse:0.07102	validation-rmse:0.07121
[170]	train-rmse:0.06582	validation-rmse:0.06606
[180]	train-rmse:0.06116	validation-rmse:0.06143
[190]	train-rmse:0.05687	validation-rmse:0.05719
[200]	train-rmse:0.05318	valida

In [23]:
import numpy as np
import pandas as pd

# PRODUCT.xlsx 데이터 로드
product_df = pd.read_excel("Dataset/PRODUCT.xlsx")

# 유클리드 거리 계산 함수 (두 점 사이의 거리 계산)
def calculate_distance(lat1, lon1, lat2, lon2):
    return np.sqrt((lat1 - lat2)**2 + (lon1 - lon2)**2)

# 예측값과 가장 가까운 상품 매칭
def match_closest_product(pred_departure_lat, pred_departure_lon, pred_destination_lat, pred_destination_lon, product_df):
    # 상품들의 출발지, 목적지 위도, 경도
    product_departure_latitudes = product_df['departure_lat']
    product_departure_longitudes = product_df['departure_long']
    product_destination_latitudes = product_df['destination_lat']
    product_destination_longitudes = product_df['destination_long']
    
    # 예측값과 각 상품의 출발지, 목적지 간의 거리 계산
    departure_distances = np.array([calculate_distance(pred_departure_lat, pred_departure_lon, lat, lon) 
                                    for lat, lon in zip(product_departure_latitudes, product_departure_longitudes)])
    destination_distances = np.array([calculate_distance(pred_destination_lat, pred_destination_lon, lat, lon)
                                      for lat, lon in zip(product_destination_latitudes, product_destination_longitudes)])

    # 출발지와 목적지의 합산 거리를 계산하여 가장 가까운 상품을 찾기
    total_distances = departure_distances + destination_distances
    closest_index = np.argmin(total_distances)
    
    # 해당 상품 정보 반환
    closest_product = product_df.iloc[closest_index]
    return closest_product

# 예측값(y_pred)와 실제값(y_test) 비교 (테스트 데이터 일부 출력)
def compare_predictions_and_actuals(y_pred, y_test, product_df, n=10):
    for i in range(n):
        # 예측값에서 출발지와 목적지 정보 추출
        predicted_departure_lat, predicted_departure_lon, predicted_destination_lat, predicted_destination_lon = y_pred[i]
        
        print(f"\n테스트 데이터 {i+1}:")
        print(f"실제값 (y_test): {y_test.iloc[i].values}")
        print(f"예측값 (y_pred): {predicted_departure_lat}, {predicted_departure_lon}, {predicted_destination_lat}, {predicted_destination_lon}")
        
        # 예측값과 가장 가까운 상품 매칭
        closest_pred_product = match_closest_product(
            predicted_departure_lat, predicted_departure_lon, 
            predicted_destination_lat, predicted_destination_lon, 
            product_df
        )
        
        print(f"\n가장 가까운 상품 (예측값과 매칭):")
        print(closest_pred_product[['product_id', 'departure_lat', 'departure_long', 'destination_lat', 'destination_long']])
        
        # 예측값과 매칭된 상품의 한글 주소 출력
        pred_product_info = product_df[product_df['product_id'] == closest_pred_product['product_id']].iloc[0]
        pred_product_departure = pred_product_info['departure']
        pred_product_destination = pred_product_info['destination']
        
        print(f"예측값 매칭 상품의 한글 주소:")
        print(f"상품 출발지: {pred_product_departure}")
        print(f"상품 목적지: {pred_product_destination}")
        
        # 실제값에서 출발지와 목적지 정보 추출
        actual_departure_lat = y_test.iloc[i]['stopover_departure_lat']
        actual_departure_lon = y_test.iloc[i]['stopover_departure_long']
        actual_destination_lat = y_test.iloc[i]['stopover_destination_lat']
        actual_destination_lon = y_test.iloc[i]['stopover_destination_long']
        
        # 실제값과 가장 가까운 상품 매칭
        closest_actual_product = match_closest_product(
            actual_departure_lat, actual_departure_lon, 
            actual_destination_lat, actual_destination_lon, 
            product_df
        )
        
        # 실제값 매칭된 상품의 한글 주소 출력
        actual_product_info = product_df[product_df['product_id'] == closest_actual_product['product_id']].iloc[0]
        actual_product_departure = actual_product_info['departure']
        actual_product_destination = actual_product_info['destination']
        
        print(f"실제값 매칭 상품의 한글 주소:")
        print(f"상품 출발지: {actual_product_departure}")
        print(f"상품 목적지: {actual_product_destination}")

# 예시: 10개 데이터 출력
compare_predictions_and_actuals(y_pred, y_test, product_df, n=10)



테스트 데이터 1:
실제값 (y_test): [ 35.27416078 128.76917983  35.5688601  127.81366454]
예측값 (y_pred): 35.349822998046875, 128.8388671875, 35.491455078125, 127.9708251953125

가장 가까운 상품 (예측값과 매칭):
product_id                 489
departure_lat        35.301454
departure_long      128.890854
destination_lat      35.611018
destination_long    127.957926
Name: 488, dtype: object
예측값 매칭 상품의 한글 주소:
상품 출발지: 경상남도 김해시 상동면 상동로 680-70
상품 목적지: 경상남도 거창군 거창읍 밤티재로 1291-10 (거창농협미곡종합처리장)
실제값 매칭 상품의 한글 주소:
상품 출발지: 경상남도 김해시 진례면 테크노밸리1로 43
상품 목적지: 경상남도 함양군 수동면 하교내백로 250-108

테스트 데이터 2:
실제값 (y_test): [ 37.3559032  127.93175726  37.20411642 127.38464713]
예측값 (y_pred): 37.33864212036133, 127.9420394897461, 37.19964599609375, 127.38619232177734

가장 가까운 상품 (예측값과 매칭):
product_id               13912
departure_lat        37.355903
departure_long      127.931757
destination_lat      37.204116
destination_long    127.384647
Name: 13911, dtype: object
예측값 매칭 상품의 한글 주소:
상품 출발지: 강원특별자치도 원주시 흥업면 원문로 816
상품 목적지: 경기도 이천시 호법면 덕평로 47

### 모델 학습 - 2차 경유지

In [25]:
import pandas as pd

result_df = pd.read_excel("Dataset/Result.xlsx")

X = result_df[['user_departure_lat', 'user_departure_long', 
                 'user_destination_lat', 'user_destination_long', 
                 'main_departure_lat', 'main_departure_long', 
                 'main_destination_lat', 'main_destination_long',
                 'first_stopover_departure_lat', 'first_stopover_departure_long', 
                 'first_stopover_destination_lat', 'first_stopover_destination_long']]

y = result_df[['second_stopover_departure_lat', 'second_stopover_departure_long',
                 'second_stopover_destination_lat', 'second_stopover_destination_long']]

# 데이터셋 나누기 (train, validation, test)
X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.3, random_state=42)
X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.5, random_state=42)

# 데이터 확인
print("\n훈련 데이터 크기:", X_train.shape, y_train.shape)
print("검증 데이터 크기:", X_val.shape, y_val.shape)
print("테스트 데이터 크기:", X_test.shape, y_test.shape)


훈련 데이터 크기: (13167, 12) (13167, 4)
검증 데이터 크기: (2822, 12) (2822, 4)
테스트 데이터 크기: (2822, 12) (2822, 4)


In [28]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_squared_error, mean_absolute_error
import xgboost as xgb

# 정규화
x_scaler = MinMaxScaler()
y_scaler = MinMaxScaler()

X_train_scaled = x_scaler.fit_transform(X_train)
joblib.dump(x_scaler, 'second_stopover_scaler.pkl') 
X_val_scaled = x_scaler.transform(X_val)
X_test_scaled = x_scaler.transform(X_test)

y_train_scaled = y_scaler.fit_transform(y_train)
y_val_scaled = y_scaler.transform(y_val)
y_test_scaled = y_scaler.transform(y_test)

# XGBoost 데이터 포맷으로 변환
dtrain = xgb.DMatrix(X_train_scaled, label=y_train_scaled)
dval = xgb.DMatrix(X_val_scaled, label=y_val_scaled)
dtest = xgb.DMatrix(X_test_scaled, label=y_test_scaled)

# 모델 파라미터 설정
params = {
    'objective': 'reg:squarederror',  # 회귀 문제
    'max_depth': 6,                   # 트리의 깊이
    'eta': 0.01,                       # 학습률
    'subsample': 0.8,                 # 데이터 샘플링 비율
    'colsample_bytree': 0.8,          # 특성 샘플링 비율
    'seed': 42,                       # 재현성 확보
    'eval_metric': 'rmse'             # 평가 지표: RMSE
}

# 학습
evals = [(dtrain, 'train'), (dval, 'validation')]
model = xgb.train(
    params,
    dtrain,
    num_boost_round=600,
    evals=evals,
    early_stopping_rounds=20,
    verbose_eval=10
)

model.save_model('Second_Stopover_Model.json')  

# 테스트 데이터 예측
y_pred_scaled = model.predict(dtest)

# 예측값 원래 스케일로 복원
y_pred = y_scaler.inverse_transform(y_pred_scaled.reshape(-1, y_train.shape[1]))

# 모델 평가
mse = mean_squared_error(y_test, y_pred)
mae = mean_absolute_error(y_test, y_pred)

print(f"\n테스트 손실(MSE): {mse:.4f}")
print(f"테스트 MAE: {mae:.4f}")

# 예측값과 실제값 비교
for i in range(5):
    print(f"\n테스트 데이터 {i+1}:")
    print(f"실제값 (y_test): {y_test.iloc[i].values}")
    print(f"예측값 (y_pred): {y_pred[i]}")

[0]	train-rmse:0.29419	validation-rmse:0.29341
[10]	train-rmse:0.26804	validation-rmse:0.26736
[20]	train-rmse:0.24398	validation-rmse:0.24339
[30]	train-rmse:0.22192	validation-rmse:0.22141
[40]	train-rmse:0.20211	validation-rmse:0.20168
[50]	train-rmse:0.18434	validation-rmse:0.18399
[60]	train-rmse:0.16853	validation-rmse:0.16825
[70]	train-rmse:0.15368	validation-rmse:0.15346
[80]	train-rmse:0.14057	validation-rmse:0.14041
[90]	train-rmse:0.12813	validation-rmse:0.12802
[100]	train-rmse:0.11727	validation-rmse:0.11722
[110]	train-rmse:0.10752	validation-rmse:0.10751
[120]	train-rmse:0.09856	validation-rmse:0.09859
[130]	train-rmse:0.09080	validation-rmse:0.09087
[140]	train-rmse:0.08355	validation-rmse:0.08365
[150]	train-rmse:0.07665	validation-rmse:0.07680
[160]	train-rmse:0.07102	validation-rmse:0.07121
[170]	train-rmse:0.06582	validation-rmse:0.06606
[180]	train-rmse:0.06116	validation-rmse:0.06143
[190]	train-rmse:0.05687	validation-rmse:0.05719
[200]	train-rmse:0.05318	valida

In [27]:
import numpy as np
import pandas as pd

# PRODUCT.xlsx 데이터 로드
product_df = pd.read_excel("Dataset/PRODUCT.xlsx")

# 유클리드 거리 계산 함수 (두 점 사이의 거리 계산)
def calculate_distance(lat1, lon1, lat2, lon2):
    return np.sqrt((lat1 - lat2)**2 + (lon1 - lon2)**2)

# 예측값과 가장 가까운 상품 매칭
def match_closest_product(pred_departure_lat, pred_departure_lon, pred_destination_lat, pred_destination_lon, product_df):
    # 상품들의 출발지, 목적지 위도, 경도
    product_departure_latitudes = product_df['departure_lat']
    product_departure_longitudes = product_df['departure_long']
    product_destination_latitudes = product_df['destination_lat']
    product_destination_longitudes = product_df['destination_long']
    
    # 예측값과 각 상품의 출발지, 목적지 간의 거리 계산
    departure_distances = np.sqrt((pred_departure_lat - product_departure_latitudes) ** 2 + 
                                  (pred_departure_lon - product_departure_longitudes) ** 2)
    destination_distances = np.sqrt((pred_destination_lat - product_destination_latitudes) ** 2 + 
                                     (pred_destination_lon - product_destination_longitudes) ** 2)

    # 출발지와 목적지의 합산 거리를 계산하여 가장 가까운 상품을 찾기
    total_distances = departure_distances + destination_distances
    closest_index = np.argmin(total_distances)
    
    # 해당 상품 정보 반환
    closest_product = product_df.iloc[closest_index]
    return closest_product

# 예측값(y_pred)와 실제값(y_test) 비교 (테스트 데이터 일부 출력)
def compare_predictions_and_actuals(y_pred, y_test, product_df, n=10):
    for i in range(n):
        # 예측값에서 출발지와 목적지 정보 추출
        predicted_departure_lat, predicted_departure_lon, predicted_destination_lat, predicted_destination_lon = y_pred[i]
        
        print(f"\n테스트 데이터 {i+1}:")
        print(f"실제값 (y_test): {y_test.iloc[i].values}")
        print(f"예측값 (y_pred): {predicted_departure_lat}, {predicted_departure_lon}, {predicted_destination_lat}, {predicted_destination_lon}")
        
        # 예측값과 가장 가까운 상품 매칭
        closest_pred_product = match_closest_product(
            predicted_departure_lat, predicted_departure_lon, 
            predicted_destination_lat, predicted_destination_lon, 
            product_df
        )
        
        print(f"\n가장 가까운 상품 (예측값과 매칭):")
        print(closest_pred_product[['product_id', 'departure_lat', 'departure_long', 'destination_lat', 'destination_long']])
        
        # 예측값과 매칭된 상품의 한글 주소 출력
        pred_product_departure = closest_pred_product['departure']
        pred_product_destination = closest_pred_product['destination']
        
        print(f"예측값 매칭 상품의 한글 주소:")
        print(f"상품 출발지: {pred_product_departure}")
        print(f"상품 목적지: {pred_product_destination}")
        
        # 실제값에서 출발지와 목적지 정보 추출
        actual_departure_lat = y_test.iloc[i]['second_stopover_departure_lat']
        actual_departure_lon = y_test.iloc[i]['second_stopover_departure_long']
        actual_destination_lat = y_test.iloc[i]['second_stopover_destination_lat']
        actual_destination_lon = y_test.iloc[i]['second_stopover_destination_long']
        
        # 실제값과 가장 가까운 상품 매칭
        closest_actual_product = match_closest_product(
            actual_departure_lat, actual_departure_lon, 
            actual_destination_lat, actual_destination_lon, 
            product_df
        )
        
        # 실제값 매칭된 상품의 한글 주소 출력
        actual_product_departure = closest_actual_product['departure']
        actual_product_destination = closest_actual_product['destination']
        
        print(f"실제값 매칭 상품의 한글 주소:")
        print(f"상품 출발지: {actual_product_departure}")
        print(f"상품 목적지: {actual_product_destination}")

# 테스트 데이터의 일부에 대해 예측값과 실제값 비교
compare_predictions_and_actuals(y_pred, y_test, product_df, n=10)


테스트 데이터 1:
실제값 (y_test): [ 36.31747618 127.32418563  35.1277254  128.6991758 ]
예측값 (y_pred): 36.31324768066406, 127.32709503173828, 35.131595611572266, 128.71775817871094

가장 가까운 상품 (예측값과 매칭):
product_id                1702
departure_lat        36.317476
departure_long      127.324186
destination_lat      35.127725
destination_long    128.699176
Name: 1701, dtype: object
예측값 매칭 상품의 한글 주소:
상품 출발지: 대전광역시 유성구 대정북로 20, 오성철강(주) 가동 (대정동)
상품 목적지: 경상남도 창원시 진해구 행암로92번안길 30 (장천동, DLC)
실제값 매칭 상품의 한글 주소:
상품 출발지: 대전광역시 유성구 대정북로 20, 오성철강(주) 가동 (대정동)
상품 목적지: 경상남도 창원시 진해구 행암로92번안길 30 (장천동, DLC)

테스트 데이터 2:
실제값 (y_test): [ 37.32536318 126.77414391  37.56480909 126.62072858]
예측값 (y_pred): 37.326297760009766, 126.77307891845703, 37.57313537597656, 126.62667846679688

가장 가까운 상품 (예측값과 매칭):
product_id                 110
departure_lat        37.325363
departure_long      126.774144
destination_lat      37.564809
destination_long    126.620729
Name: 109, dtype: object
예측값 매칭 상품의 한글 주소:
상품 출발지: 경기도 안산시 단원구 해

### prediction

#### 1차 경로 예측

In [28]:
from geopy.distance import geodesic

def calculate_distance(lat1, long1, lat2, long2):
    return geodesic((lat1, long1), (lat2, long2)).km

In [29]:
import pandas as pd
import numpy as np
import xgboost as xgb
from sklearn.preprocessing import StandardScaler

# 첫 번째 경로 예측 함수
def predict_first_route(model_first, X_first_scaled):
    dtest_first = xgb.DMatrix(X_first_scaled)  # DataFrame을 DMatrix로 변환
    y_pred_first = model_first.predict(dtest_first)
    return y_pred_first  # 예측된 1차 경로 (departure_lat, departure_long, destination_lat, destination_long)

# 가장 가까운 상품 매칭 함수
def match_closest_product(pred_departure_lat, pred_departure_lon, pred_destination_lat, pred_destination_lon, product_df):
    # 상품들의 출발지, 목적지 위도, 경도
    product_departure_latitudes = product_df['departure_lat']
    product_departure_longitudes = product_df['departure_long']
    product_destination_latitudes = product_df['destination_lat']
    product_destination_longitudes = product_df['destination_long']
    
    # 예측값과 각 상품의 출발지, 목적지 간의 거리 계산
    departure_distances = np.sqrt((pred_departure_lat - product_departure_latitudes) ** 2 + 
                                  (pred_departure_lon - product_departure_longitudes) ** 2)
    destination_distances = np.sqrt((pred_destination_lat - product_destination_latitudes) ** 2 + 
                                     (pred_destination_lon - product_destination_longitudes) ** 2)

    # 출발지와 목적지의 합산 거리를 계산하여 가장 가까운 상품을 찾기
    total_distances = departure_distances + destination_distances
    closest_index = np.argmin(total_distances)
    
    # 해당 상품 정보 반환
    closest_product = product_df.iloc[closest_index]
    return closest_product

# 첫 번째 경로 예측 및 상품 매칭 함수
def predict_and_match_first_route(file_path, product_file_path, model_file_path, output_file_path):
    # 데이터 로드
    X_first = pd.read_excel(file_path)
    product_df = pd.read_excel(product_file_path)

    # 'departure_time' 열이 있으면 datetime 변환
    if 'departure_time' in X_first.columns:
        X_first['departure_time'] = pd.to_datetime(X_first['departure_time']).astype(int) / 10**9

    # 필요 없는 열 제거
    if 'departure' in X_first.columns and X_first['departure'].dtype == 'object':
        X_first.drop(columns=['departure'], inplace=True)

    if 'destination' in X_first.columns and X_first['destination'].dtype == 'object':
        X_first.drop(columns=['destination'], inplace=True)
    
    X_first.drop(columns=['user_id'], inplace=True)

    # 특징 컬럼 정의
    feature_cols = ['departure_lat', 'departure_long', 'destination_lat', 
                    'destination_long', 'preference']

    # 정규화: StandardScaler 사용
    scaler = StandardScaler()
    X_first_scaled = scaler.fit_transform(X_first[feature_cols])

    # 모델 로드
    model_first = xgb.Booster()
    model_first.load_model(model_file_path)

    # 첫 번째 경로 예측
    first_route_predictions = predict_first_route(model_first, X_first_scaled)

    closest_products = []

    # 예측된 1차 경로에 대해 상품 매칭
    for i, pred in enumerate(first_route_predictions):
        pred_departure_lat = pred[0]
        pred_departure_lon = pred[1]
        pred_destination_lat = pred[2]
        pred_destination_lon = pred[3]

        X_first_row = X_first.iloc[i]

        closest_product = match_closest_product(pred_departure_lat, pred_departure_lon,
                                                pred_destination_lat, pred_destination_lon, product_df)
        
        if closest_product is not None:
            # 매칭된 상품의 weight를 누적 무게로 설정
            product_weight = closest_product['weight']
            closest_products.append({
                'departure_lat': X_first_row['departure_lat'],
                'departure_long': X_first_row['departure_long'],
                'destination_lat': X_first_row['destination_lat'],
                'destination_long': X_first_row['destination_long'],
                'closest_product_departure_lat': closest_product['departure_lat'],
                'closest_product_departure_long': closest_product['departure_long'],
                'closest_product_destination_lat': closest_product['destination_lat'],
                'closest_product_destination_long': closest_product['destination_long'],
                'product_weight': product_weight,
                'closest_products': closest_product.to_dict()
            })
            print(f"매칭 성공")
        else:
            print(f"매칭 실패")

    # 결과를 DataFrame으로 변환 후 저장
    closest_products_df = pd.DataFrame(closest_products)
    closest_products_df.to_csv(output_file_path, index=False)

    return closest_products_df

#### 1차 경유지 예측

In [30]:
import pandas as pd
import numpy as np
import xgboost as xgb
from sklearn.preprocessing import MinMaxScaler

# 1차 경유지 예측 함수
def predict_stopover(model_stopover, X_stopover_scaled):
    dtest_stopover = xgb.DMatrix(X_stopover_scaled)  # DataFrame을 DMatrix로 변환
    y_pred_stopover = model_stopover.predict(dtest_stopover)
    return y_pred_stopover  

# 가장 가까운 상위 N개의 상품 매칭 함수
def match_top_n_products(pred_departure_lat, pred_departure_lon, pred_destination_lat, pred_destination_lon, product_df, n=3):
    # 상품들의 출발지, 목적지 위도, 경도
    product_departure_latitudes = product_df['departure_lat']
    product_departure_longitudes = product_df['departure_long']
    product_destination_latitudes = product_df['destination_lat']
    product_destination_longitudes = product_df['destination_long']

    # 예측값과 각 상품의 출발지, 목적지 간의 거리 계산
    departure_distances = np.sqrt((pred_departure_lat - product_departure_latitudes) ** 2 + 
                                  (pred_departure_lon - product_departure_longitudes) ** 2)
    destination_distances = np.sqrt((pred_destination_lat - product_destination_latitudes) ** 2 + 
                                     (pred_destination_lon - product_destination_longitudes) ** 2)

    # 출발지와 목적지의 합산 거리 계산
    total_distances = departure_distances + destination_distances

    # 가장 가까운 거리의 상위 N개 상품 인덱스
    top_n_indices = np.argsort(total_distances)[:n]
    top_n_products = product_df.iloc[top_n_indices]

    return top_n_products

# 데이터 로드 및 경유지 예측 수행 함수
def predict_stopovers_and_match(file_path, closest_products_file, product_file_path, model_file_path, output_file_path):
    # 데이터 로드
    X_first = pd.read_excel(file_path)
    closest_products_df = pd.read_csv(closest_products_file)
    product_df = pd.read_excel(product_file_path)

    # 1차 경로 예측값과 상품 매칭 결과 결합
    stopover_input = pd.concat([  
        X_first[['departure_lat', 'departure_long', 'destination_lat', 'destination_long']],  # 1차 경로 예측값
        closest_products_df[['closest_product_departure_lat', 'closest_product_departure_long', 
                             'closest_product_destination_lat', 'closest_product_destination_long']]  # 상품 매칭 결과
    ], axis=1)

    # 정규화: MinMaxScaler 사용
    feature_cols_stopover = ['departure_lat', 'departure_long', 'destination_lat', 'destination_long',
                             'closest_product_departure_lat', 'closest_product_departure_long', 
                             'closest_product_destination_lat', 'closest_product_destination_long']
    
    # 스케일러 생성
    scaler_stopover = MinMaxScaler()
    
    # 입력 데이터 정규화
    X_stopover_scaled = scaler_stopover.fit_transform(stopover_input[feature_cols_stopover])

    # 모델 로드
    model_stopover = xgb.Booster()
    model_stopover.load_model(model_file_path)

    # 1차 경유지 예측
    stopover_predictions_scaled = predict_stopover(model_stopover, X_stopover_scaled)
    stopover_predictions_scaled = stopover_predictions_scaled.reshape(-1, 4)
    stopover_predictions_scaled = np.hstack([stopover_predictions_scaled, np.zeros((stopover_predictions_scaled.shape[0], 4))])
    stopover_predictions = scaler_stopover.inverse_transform(stopover_predictions_scaled)
    
    results = []

    # 예측된 1차 경유지 출력 및 상품 매칭
    for i, pred in enumerate(stopover_predictions): 
        stopover_departure_lat = pred[0]
        stopover_departure_lon = pred[1]
        stopover_destination_lat = pred[2]
        stopover_destination_lon = pred[3]
    
        # 가장 가까운 상위 3개의 상품 찾기
        top_products = match_top_n_products(stopover_departure_lat, stopover_departure_lon,
                                            stopover_destination_lat, stopover_destination_lon, 
                                            product_df, n=3)
        
        stopover_input_row = stopover_input.iloc[i]

        # 결과 저장
        for _, product in top_products.iterrows():
            result = {
                'user_departure_lat': stopover_input_row['departure_lat'],
                'user_departure_long': stopover_input_row['departure_long'],
                'user_destination_lat': stopover_input_row['destination_lat'],
                'user_destination_long': stopover_input_row['destination_long'],
                'main_departure_lat': stopover_input_row['closest_product_departure_lat'],
                'main_departure_long': stopover_input_row['closest_product_departure_long'],
                'main_destination_lat': stopover_input_row['closest_product_destination_lat'],
                'main_destination_long': stopover_input_row['closest_product_destination_long'],
                'stopover_departure_lat': product['departure_lat'],
                'stopover_departure_lon': product['departure_long'],
                'stopover_destination_lat': product['destination_lat'],
                'stopover_destination_lon': product['destination_long'],
                'product_price': product['price'],
                'product_weight': product['weight']
            }
            results.append(result)

    # 결과를 DataFrame으로 변환 후 CSV로 저장
    df_results = pd.DataFrame(results)
    df_results.to_csv(output_file_path, index=False)

    return df_results

#### 2차 경유지 예측 

In [31]:
import pandas as pd
import numpy as np
import xgboost as xgb
from sklearn.preprocessing import MinMaxScaler

# 2차 경유지 예측 함수
def predict_second_stopover(model, X_scaled):
    dtest = xgb.DMatrix(X_scaled)  # DataFrame을 DMatrix로 변환
    y_pred = model.predict(dtest)  # 예측
    return y_pred  

# 가장 가까운 상품 찾기 함수 (예시: 거리 기반으로 상품을 찾는 함수)
def match_closest_product(departure_lat, departure_lon, destination_lat, destination_lon, product_df):
    # 상품들의 출발지, 목적지 위도, 경도
    product_departure_latitudes = product_df['departure_lat']
    product_departure_longitudes = product_df['departure_long']
    product_destination_latitudes = product_df['destination_lat']
    product_destination_longitudes = product_df['destination_long']

    # 예측값과 각 상품의 출발지, 목적지 간의 거리 계산
    departure_distances = np.sqrt((departure_lat - product_departure_latitudes) ** 2 + 
                                  (departure_lon - product_departure_longitudes) ** 2)
    destination_distances = np.sqrt((destination_lat - product_destination_latitudes) ** 2 + 
                                     (destination_lon - product_destination_longitudes) ** 2)

    # 출발지와 목적지의 합산 거리 계산
    total_distances = departure_distances + destination_distances

    # 가장 가까운 상품 인덱스
    closest_product_index = np.argmin(total_distances)
    closest_product = product_df.iloc[closest_product_index]

    return closest_product

# 2차 경유지 예측 및 상품 매칭 함수
def predict_second_stopovers_and_match(stopover_input_file, model_path, product_df, output_file_path):
    # 데이터 로드
    second_stopover_input = pd.read_csv(stopover_input_file)

    # 입력 데이터 결합
    second_stopover_input_combined = pd.concat([  
        second_stopover_input[['user_departure_lat', 'user_departure_long', 'user_destination_lat', 'user_destination_long']],
        second_stopover_input[['main_departure_lat', 'main_departure_long', 'main_destination_lat', 'main_destination_long']],
        second_stopover_input[['stopover_departure_lat', 'stopover_departure_lon', 'stopover_destination_lat', 'stopover_destination_lon']]
    ], axis=1)

    # 정규화: MinMaxScaler 사용
    feature_cols_stopover = ['user_departure_lat', 'user_departure_long', 'user_destination_lat', 'user_destination_long',
                             'main_departure_lat', 'main_departure_long', 'main_destination_lat', 'main_destination_long',
                             'stopover_departure_lat', 'stopover_departure_lon', 'stopover_destination_lat', 'stopover_destination_lon']
    
    # 스케일러 생성 및 입력 데이터 정규화
    second_scaler_stopover = MinMaxScaler()
    second_X_stopover_scaled = second_scaler_stopover.fit_transform(second_stopover_input_combined[feature_cols_stopover])

    # 2차 경유지 예측 모델 로드
    model_second_stopover = xgb.Booster()
    model_second_stopover.load_model(model_path)
    
    second_stopover_predictions_scaled = predict_second_stopover(model_second_stopover, second_X_stopover_scaled)
    second_stopover_predictions_scaled = second_stopover_predictions_scaled.reshape(-1, 4)
    second_stopover_predictions_scaled = np.hstack([second_stopover_predictions_scaled, np.zeros((second_stopover_predictions_scaled.shape[0], 8))])
    second_stopover_predictions = second_scaler_stopover.inverse_transform(second_stopover_predictions_scaled)

    # 예측 결과를 저장할 리스트
    results_2nd = []
    
    # 예측된 2차 경유지 출력 및 상품 매칭
    for i, pred in enumerate(second_stopover_predictions): 
        second_stopover_departure_lat = pred[0]
        second_stopover_departure_lon = pred[1]
        second_stopover_destination_lat = pred[2]
        second_stopover_destination_lon = pred[3]
        
        # 가장 가까운 상품 찾기
        closest_product = match_closest_product(second_stopover_departure_lat, second_stopover_departure_lon,
                                                second_stopover_destination_lat, second_stopover_destination_lon,
                                                product_df)
        
        second_stopover_input_row = second_stopover_input.iloc[i]
        
        # 결과 저장
        result_2nd = {
            'user_departure_lat': second_stopover_input_row['user_departure_lat'],
            'user_departure_long': second_stopover_input_row['user_departure_long'],
            'user_destination_lat': second_stopover_input_row['user_destination_lat'],
            'user_destination_long': second_stopover_input_row['user_destination_long'],
            'main_departure_lat': second_stopover_input_row['main_departure_lat'],
            'main_departure_long': second_stopover_input_row['main_departure_long'],
            'main_destination_lat': second_stopover_input_row['main_destination_lat'],
            'main_destination_long': second_stopover_input_row['main_destination_long'],
            'stopover_departure_lat': second_stopover_input_row['stopover_departure_lat'],
            'stopover_departure_lon': second_stopover_input_row['stopover_departure_lon'],
            'stopover_destination_lat': second_stopover_input_row['stopover_destination_lat'],
            'stopover_destination_lon': second_stopover_input_row['stopover_destination_lon'],
            'second_stopover_departure_lat': closest_product['departure_lat'],
            'second_stopover_departure_lon': closest_product['departure_long'],
            'second_stopover_destination_lat': closest_product['destination_lat'],
            'second_stopover_destination_lon': closest_product['destination_long'],
            'closest_product': closest_product.to_dict()
        }
        results_2nd.append(result_2nd)

        # 예측 결과 출력
        print(f"예측된 2차 경유지 {i+1}:")
        print(f"  경유지 출발지 위도: {second_stopover_departure_lat}, 경도: {second_stopover_departure_lon}")
        print(f"  경유지 목적지 위도: {second_stopover_destination_lat}, 경도: {second_stopover_destination_lon}")
        print("-" * 50)

    # 예측 결과를 DataFrame으로 변환
    df_results_2nd = pd.DataFrame(results_2nd)

    # 결과 파일로 저장
    df_results_2nd.to_csv(output_file_path, index=False)

    return df_results_2nd


### PREDICT_ALL

In [16]:
# 전체 예측 및 매칭을 순차적으로 수행하는 함수
def predict_and_match_all(input_path, output_file_path):
    
    product_file_path = 'Dataset/PRODUCT.xlsx'  # 상품 데이터 파일 경로
    model_file_path_first_route = 'Models/First_Route_Model.json'  # 1차 경로 예측 모델 경로
    model_file_path_first_stopover = 'Models/First_Stopover_Model.json'  # 1차 경유지 예측 모델 경로
    model_file_path_second_stopover = 'Models/Second_Stopover_Model.json'  # 2차 경유지 예측 모델 경로
    
    file_path = 'stopover_predictions_with_top_3_products.csv'  
    closest_products_file = 'closest_products.csv'  # 가장 가까운 상품 파일 경로
    
    # 1차 경로 예측 및 매칭
    predict_and_match_first_route(input_path, product_file_path, model_file_path_first_route, closest_products_file)
    
    # 1차 경유지 예측 및 상품 매칭
    predict_stopovers_and_match(input_path, closest_products_file, product_file_path, model_file_path_first_stopover, file_path)
    
    # 2차 경유지 예측 및 상품 매칭
    stopover_input_file = 'stopover_predictions_with_top_3_products.csv'  # 1차 경유지 예측 결과 파일
    product_df = pd.read_excel(product_file_path)  # 상품 데이터 로드
    predict_second_stopovers_and_match(stopover_input_file, model_file_path_second_stopover, product_df, output_file_path)
    
    print("모든 예측 및 매칭 과정 완료!")

# 실행 예시
if __name__ == "__main__":
    # 파일 경로 및 모델 파일 경로 설정
    input_path = 'INPUT.xlsx'

    output_file_path = 'final_predictions.csv'  # 최종 예측 결과 파일 경로

    # 전체 예측 및 매칭 수행
    predict_and_match_all(input_path, output_file_path)

/tmp/ipykernel_218678/2095868807.py:42: FutureWarning: casting datetime64[ns] values to int64 with .astype(...) is deprecated and will raise in a future version. Use .view(...) instead.
  X_first['departure_time'] = pd.to_datetime(X_first['departure_time']).astype(int) / 10**9


매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성공
매칭 성

* 위도 경도 값에 해당하는 주소지 확인

In [64]:
import pandas as pd
import numpy as np

# 데이터 로드
second_stopover_df = pd.read_csv('second_stopover_predictions_limited.csv')  # 예측된 경로 데이터
product_df = pd.read_excel('Dataset/PRODUCT.xlsx')  # 상품 정보 데이터
input_df = pd.read_excel('INPUT.xlsx')

# 상위 10개 경로에 대해 처리
top_10_rows = second_stopover_df.head(10)

# 결과 저장을 위한 리스트
results = []

def match_product_by_coordinates(departure_lat, departure_lon, destination_lat, destination_lon):
    # PRODUCT.xlsx에서 일치하는 상품 찾기
    matched_product = product_df[
        (product_df['departure_lat'] == departure_lat) & 
        (product_df['departure_long'] == departure_lon) & 
        (product_df['destination_lat'] == destination_lat) & 
        (product_df['destination_long'] == destination_lon)
    ]
    
    if not matched_product.empty:
        # 일치하는 상품이 있으면 product_id, departure, destination을 반환
        matched_product_id = matched_product['product_id'].values[0]
        matched_departure = matched_product['departure'].values[0]
        matched_destination = matched_product['destination'].values[0]
        
        return {
            'product_id': matched_product_id,
            'departure': matched_departure,
            'destination': matched_destination
        }
    else:
        return None  # 일치하는 상품이 없을 경우 None 반환
    
def match_input_by_coordinates(departure_lat, departure_lon, destination_lat, destination_lon):
    # INPUT.xlsx에서 일치하는 상품 찾기
    matched_product = input_df[
        (input_df['departure_lat'] == departure_lat) & 
        (input_df['departure_long'] == departure_lon) & 
        (input_df['destination_lat'] == destination_lat) & 
        (input_df['destination_long'] == destination_lon)
    ]
    
    if not matched_product.empty:
        # 일치하는 상품이 있으면 product_id, departure, destination을 반환
        matched_product_id = matched_product['user_id'].values[0]
        matched_departure = matched_product['departure'].values[0]
        matched_destination = matched_product['destination'].values[0]
        
        return {
            'user_id': matched_product_id,
            'departure': matched_departure,
            'destination': matched_destination
        }
    else:
        return None  # 일치하는 상품이 없을 경우 None 반환

# 각 경로에 대해 가장 가까운 상품을 찾고 결과 저장
for index, row in top_10_rows.iterrows():
    print('-------------------------------------------------------------------------------------------')
    user_departure_lat = row['user_departure_lat']
    user_departure_long = row['user_departure_long']
    user_destination_lat = row['user_destination_lat']
    user_destination_long = row['user_destination_long']
    
    user_result = match_input_by_coordinates(user_departure_lat, user_departure_long, user_destination_lat, user_destination_long)
    print(f"기사 경로: {user_result}")
    
    main_departure_lat = row['main_departure_lat']
    main_departure_long = row['main_departure_long']
    main_destination_lat = row['main_destination_lat']
    main_destination_long = row['main_destination_long']
    
    main_result = match_product_by_coordinates(main_departure_lat, main_departure_long, main_destination_lat, main_destination_long)
    print(f"1차 물류 경로:{main_result}")
    
    stopover_departure_lat = row['stopover_departure_lat']
    stopover_departure_lon =  row['stopover_departure_lon']
    stopover_destination_lat = row['stopover_destination_lat']
    stopover_destination_lon = row['stopover_destination_lon']
    
    stopover_result = match_product_by_coordinates(stopover_departure_lat, stopover_departure_lon, stopover_destination_lat, stopover_destination_lon)
    print(f"1차 경유지 경로:{stopover_result}")
    
    second_stopover_departure_lat = row['second_stopover_departure_lat']
    second_stopover_departure_lon = row['second_stopover_departure_lon']
    second_stopover_destination_lat = row['second_stopover_destination_lat']
    second_stopover_destination_lon = row['second_stopover_destination_lon']
    
    second_stopover_result = match_product_by_coordinates(second_stopover_departure_lat, second_stopover_departure_lon, second_stopover_destination_lat, second_stopover_destination_lon)
    print(f"2차 경유지 경로:{second_stopover_result}")

# 결과를 DataFrame으로 변환
results_df = pd.DataFrame(results)
print(results_df)

# 결과를 CSV로 저장
# results_df.to_csv('second_stopover_with_product_info.csv', index=False)

-------------------------------------------------------------------------------------------
기사 경로: {'user_id': 412, 'departure': '경기도 평택시 서탄면 수월암2길 23-20', 'destination': '전라남도 구례군 구례읍 백련리 571-1'}
1차 물류 경로:{'product_id': 6102, 'departure': '경기도 의왕시 오봉산단3로 60, 의왕 물류센터 5층 (삼동)', 'destination': '전북특별자치도 남원시 사매면 대사로 1375, 전북 지리산 낙농농협 사매 물류사업소'}
1차 경유지 경로:{'product_id': 7994, 'departure': '서울특별시 서초구 양재대로12길 25 (양재동)', 'destination': '충청남도 논산시 연무읍 동안로 718'}
2차 경유지 경로:{'product_id': 5612, 'departure': '전북특별자치도 완주군 봉동읍 완주산단2로 282-22', 'destination': '경상남도 함양군 수동면 수동길 37'}
-------------------------------------------------------------------------------------------
기사 경로: {'user_id': 412, 'departure': '경기도 평택시 서탄면 수월암2길 23-20', 'destination': '전라남도 구례군 구례읍 백련리 571-1'}
1차 물류 경로:{'product_id': 6102, 'departure': '경기도 의왕시 오봉산단3로 60, 의왕 물류센터 5층 (삼동)', 'destination': '전북특별자치도 남원시 사매면 대사로 1375, 전북 지리산 낙농농협 사매 물류사업소'}
1차 경유지 경로:{'product_id': 4717, 'departure': '서울특별시 구로구 신도림로19길 53 (신도림동)', 'destinatio

* 지도 plot

In [65]:
import folium
import webbrowser


def plot_locations_on_map(locations):
    if len(locations) != 8:
        raise ValueError("위도, 경도 값은 총 8개여야 합니다.")
    
    # 지도 중앙 위치를 첫 번째 위치의 위도, 경도로 설정
    map_center = locations[0]
    m = folium.Map(location=map_center, zoom_start=12)  # 시작 위치와 줌 레벨 설정

    # 각 위치에 마커 추가
    labels = ['기사 출발지', '기사 목적지', '1차 물류 출발지', '1차 물류 목적지', '경유지 1 출발지', '경유지 1 목적지', '경유지 2 출발지', '경유지 2 목적지']
    
    for i, (lat, lon) in enumerate(locations):
        folium.Marker([lat, lon], popup=labels[i]).add_to(m)
        
    return m

top_rows = second_stopover_df.head(10)
for index, row in top_rows.iterrows():
    
    locations = [
        (row['user_departure_lat'], row['user_departure_long']),  
        (row['user_destination_lat'], row['user_destination_long']), 
        (row['main_departure_lat'], row['main_departure_long']),  
        (row['main_destination_lat'], row['main_destination_long']), 
        (row['stopover_departure_lat'], row['stopover_departure_lon']),  
        (row['stopover_destination_lat'], row['stopover_destination_lon']), 
        (row['second_stopover_departure_lat'], row['second_stopover_departure_lon']),  
        (row['second_stopover_destination_lat'], row['second_stopover_destination_lon']), 
    ]   

    # 지도 생성 및 출력
    map_with_locations = plot_locations_on_map(locations)
    map_with_locations.save(f"Maps/locations_map_{index}.html")  

* Front server로 보낼 프레임: 
    * 경유지 리스트: 경유지명 (창고이름), 물품명, 비용, 무게, 위도, 경도, 한글주소, 물류 ID, 경로 ID 
    * 경유지 개수: 2
    * 총 소요시간
    * 총 운송무게
    * 총 운행거리